In [164]:
from nas_201_api import NASBench201API as API
from nas_201_api import ResultsCount
from nas_201_api import ArchResults
import torch
import numpy as np
from scipy import stats
import pandas as pd

# Creating an API instance from a file:

In [50]:
api = API('/home/gean/datasets/NAS-Bench-201-v1_1-096897.pth')
api

try to create the NAS-Bench-201 api from /home/gean/datasets/NAS-Bench-201-v1_1-096897.pth


NASBench201API(15625/15625 architectures, file=NAS-Bench-201-v1_1-096897.pth)

#### [2020.03.16] NAS-Bench-201-v1_1-096897.pth : 2225 architectures are trained once, 5439 archiitectures are trained twice, 7961 architectures are trained three times on all training sets. For the hyper-parameters with the total epochs of 12, each model is trained on CIFAR-10, CIFAR-100, ImageNet16-120 once, and is trained on CIFAR-10-VALID twice.

In [269]:
print("####### 12 epochs #######")
print("cifar10-valid:", api.statistics('cifar10-valid', 12))
print("cifar10:", api.statistics('cifar10', 12))
print("cifar100:", api.statistics('cifar100', 12))
print("ImageNet16-120:", api.statistics('ImageNet16-120', 12))

print("\n####### 200 epochs #######")
print("cifar10-valid:", api.statistics('cifar10-valid', 200))
print("cifar10:", api.statistics('cifar10', 200))
print("cifar100:", api.statistics('cifar100', 200))
print("ImageNet16-120:", api.statistics('ImageNet16-120', 200))

####### 12 epochs #######
Call the statistics function with dataset=cifar10-valid and hp=12.
cifar10-valid: {2: 15625}
Call the statistics function with dataset=cifar10 and hp=12.
cifar10: {1: 15625}
Call the statistics function with dataset=cifar100 and hp=12.
cifar100: {1: 15625}
Call the statistics function with dataset=ImageNet16-120 and hp=12.
ImageNet16-120: {1: 15625}

####### 200 epochs #######
Call the statistics function with dataset=cifar10-valid and hp=200.
cifar10-valid: {3: 7961, 2: 5439, 1: 2225}
Call the statistics function with dataset=cifar10 and hp=200.
cifar10: {3: 7961, 2: 5439, 1: 2225}
Call the statistics function with dataset=cifar100 and hp=200.
cifar100: {3: 7961, 2: 5439, 1: 2225}
Call the statistics function with dataset=ImageNet16-120 and hp=200.
ImageNet16-120: {3: 7961, 2: 5439, 1: 2225}


# Show the number of architectures len(api) and each architecture api[i]:

In [204]:
print("number of archs: ", len(api))

for i, arch_str in enumerate(api):
#     layers = extract_layers(api, arch_str)
    info = api.query_meta_info_by_index(i, hp='200') 
    print('{:} \n{:5d}/{:5d} : {:}'.format(info, i, len(api), arch_str))

number of archs:  15625
Call query_meta_info_by_index with arch_index=0, hp=200
ArchResults(arch-index=0, arch=|avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~1|+|nor_conv_1x1~0|skip_connect~1|skip_connect~2|, 12 runs, clear=True) 
    0/15625 : |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~1|+|nor_conv_1x1~0|skip_connect~1|skip_connect~2|
Call query_meta_info_by_index with arch_index=1, hp=200
ArchResults(arch-index=1, arch=|nor_conv_3x3~0|+|nor_conv_3x3~0|avg_pool_3x3~1|+|skip_connect~0|nor_conv_3x3~1|skip_connect~2|, 12 runs, clear=True) 
    1/15625 : |nor_conv_3x3~0|+|nor_conv_3x3~0|avg_pool_3x3~1|+|skip_connect~0|nor_conv_3x3~1|skip_connect~2|
Call query_meta_info_by_index with arch_index=2, hp=200
ArchResults(arch-index=2, arch=|avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~1|+|avg_pool_3x3~0|avg_pool_3x3~1|avg_pool_3x3~2|, 12 runs, clear=True) 
    2/15625 : |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~1|+|avg_pool_3x3~0|avg_pool_3x3~1|avg_pool_3x3~2|
Call query_meta_info_by_inde

# Specify an architecture to play around

In [111]:
arch = 15624

# Show the results of all trials for a single architecture:

In [112]:
api.show(arch)

>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>> 012 epochs >>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>
|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|
datasets : ['cifar10-valid', 'cifar10', 'cifar100', 'ImageNet16-120'], extra-info : None
cifar10-valid  FLOP= 23.51 M, Params=0.185 MB, latency=19.55 ms.
cifar10-valid  train : [loss = 1.216, top1 = 56.05%], valid : [loss = 1.222, top1 = 55.76%]
cifar10        FLOP= 23.51 M, Params=0.185 MB, latency=19.55 ms.
cifar10        train : [loss = 0.965, top1 = 65.83%], test  : [loss = 0.944, top1 = 66.67%]
cifar100       FLOP= 23.52 M, Params=0.191 MB, latency=19.33 ms.
cifar100       train : [loss = 2.945, top1 = 25.85%], valid : [loss = 2.939, top1 = 25.28%], test : [loss = 2.947, top1 = 25.36%]
ImageNet16-120 FLOP=  5.89 M, Params=0.192 MB, latency=20.88 ms.
ImageNet16-120 train : [loss = 3.749, top1 = 12.89%], valid : [loss = 3.698, top1 = 13.43%], test : [loss = 3.716, top1 = 13.27%]
>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>

In [120]:
# show the mean loss and accuracy of an architecture
info = api.query_meta_info_by_index(arch)  # This is an instance of `ArchResults`
print("info: ", info)

res_metrics = info.get_metrics('cifar10', 'train') # This is a dict with metric names as keys
print("\nres_metrics: ", res_metrics)

cost_metrics = info.get_compute_costs('cifar10') # This is a dict with metric names as keys, e.g., flops, params, latency
print("\ncost_metrics: ", cost_metrics)

Call query_meta_info_by_index with arch_index=15624, hp=12
info:  ArchResults(arch-index=15624, arch=|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|, 5 runs, clear=True)

res_metrics:  {'iepoch': 11.0, 'loss': 0.9650854194641113, 'accuracy': 65.826, 'cur_time': 20.893992225329082, 'all_time': 250.72790670394895}

cost_metrics:  {'flops': 23.51169, 'params': 0.185306, 'latency': 0.019546220177098325, 'T-train@epoch': 20.89399222532908, 'T-train@total': 250.72790670394895, 'T-ori-test@epoch': 1.2722857111976258, 'T-ori-test@total': 15.26742853437151}


Call query_index_by_arch with arch=1


TypeError: 'NoneType' object is not callable

In [99]:
# get the detailed information
results = api.query_by_index(arch, 'cifar100') # a dict of all trials for 1st net on cifar10, where the key is the seed
print("\nresults: ", results)

print('\nThere are {:} trials for this architecture [{:}] on cifar100'.format(len(results), api[arch]))

for seed, result in results.items():
    print('\nLatency : {:}'.format(result.get_latency()))
    print('Train Info : {:}'.format(result.get_train()))
    print('Valid Info : {:}'.format(result.get_eval('x-valid')))
    print('Test  Info : {:}'.format(result.get_eval('x-test')))
    
    # for the metric after a specific epoch
    print('Train Info [10-th epoch] : {:}'.format(result.get_train(10)))

Call query_by_index with arch_index=15624, dataname=cifar100, hp=12
Call query_meta_info_by_index with arch_index=15624, hp=12

results:  {111: ResultsCount(cifar100, arch=|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|, FLOP=23.52M, Param=0.191MB, seed=0111, 3 eval-sets: [x-test, x-valid, ori-test])}

There are 1 trials for this architecture [|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|] on cifar100

Latency : 0.019329755394547076
Train Info : {'iepoch': 11, 'loss': 2.9447394641113283, 'accuracy': 25.854, 'cur_time': 20.893992225329082, 'all_time': 250.72790670394895}
Valid Info : {'iepoch': 11, 'loss': 2.939332267379761, 'accuracy': 25.279999975585937, 'cur_time': 0.636142855598813, 'all_time': 7.633714267185755}
Test  Info : {'iepoch': 11, 'loss': 2.9470318691253663, 'accuracy': 25.36, 'cur_time': 0.636142855598813, 'all_time': 7.633714267185755}
Train Info [10-th epoch] : {'iepoch': 10, 'loss': 2.987324168167114, 'a

In [121]:
# get the detailed information
# results = api.query_meta_info_by_index(arch) 
# print("\nresults query meta: ", results)

results = api.query_by_index(arch, 'cifar100') # a dict of all trials for 1st net on cifar10, where the key is the seed
print("\nresults 1: ", results)

results = api.query_by_index(arch, hp='12')
print("\nresults 2: ", results)


Call query_by_index with arch_index=15624, dataname=cifar100, hp=12
Call query_meta_info_by_index with arch_index=15624, hp=12

results 1:  {111: ResultsCount(cifar100, arch=|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|, FLOP=23.52M, Param=0.191MB, seed=0111, 3 eval-sets: [x-test, x-valid, ori-test])}
Call query_by_index with arch_index=15624, dataname=None, hp=12
Call query_meta_info_by_index with arch_index=15624, hp=12

results 2:  ArchResults(arch-index=15624, arch=|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|, 5 runs, clear=True)


In [105]:
# get the detailed information
results = api.query_by_index(arch, 'cifar10') # a dict of all trials for 1st net on cifar10, where the key is the seed
print("\nresults: ", results)

print('\nThere are {:} trials for this architecture [{:}] on cifar100'.format(len(results), api[arch]))

for seed, result in results.items():
    print('\nLatency : {:}'.format(result.get_latency()))
    print('Train Info : {:}'.format(result.get_train()))
    print('Valid Info : {:}'.format(result.get_eval('x-valid')))
    print('Test  Info : {:}'.format(result.get_eval('x-test')))
    
    # for the metric after a specific epoch
    print('Train Info [10-th epoch] : {:}'.format(result.get_train(10)))

Call query_by_index with arch_index=15624, dataname=cifar10, hp=12
Call query_meta_info_by_index with arch_index=15624, hp=12

results:  {111: ResultsCount(cifar10, arch=|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|, FLOP=23.51M, Param=0.185MB, seed=0111, 1 eval-sets: [ori-test])}

There are 1 trials for this architecture [|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|] on cifar100

Latency : 0.019546220177098325
Train Info : {'iepoch': 11, 'loss': 0.9650854194641113, 'accuracy': 65.826, 'cur_time': 20.893992225329082, 'all_time': 250.72790670394895}


KeyError: 'x-valid@11'

# Query the index of an architecture by string

In [17]:
index = api.query_index_by_arch('|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|')
api.show(index)

Call query_index_by_arch with arch=|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|
>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>> 012 epochs >>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>
|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|
datasets : ['cifar10-valid', 'cifar10', 'cifar100', 'ImageNet16-120'], extra-info : None
cifar10-valid  FLOP= 23.51 M, Params=0.185 MB, latency=19.55 ms.
cifar10-valid  train : [loss = 1.216, top1 = 56.05%], valid : [loss = 1.222, top1 = 55.76%]
cifar10        FLOP= 23.51 M, Params=0.185 MB, latency=19.55 ms.
cifar10        train : [loss = 0.965, top1 = 65.83%], test  : [loss = 0.944, top1 = 66.67%]
cifar100       FLOP= 23.52 M, Params=0.191 MB, latency=19.33 ms.
cifar100       train : [loss = 2.945, top1 = 25.85%], valid : [loss = 2.939, top1 = 25.28%], test : [loss = 2.947, top1 = 25.36%]
ImageNet16-120 FLOP=  5.89 M, Params=0.192 MB, latency=20.88 ms.
ImageNet16-120 train : [loss = 3.749, top1 = 12.8

In [18]:
# This string |nor_conv_3x3~0|+|nor_conv_3x3~0|avg_pool_3x3~1|+|skip_connect~0|nor_conv_3x3~1|skip_connect~2| means:

# node-0: the input tensor
# node-1: conv-3x3( node-0 )
# node-2: conv-3x3( node-0 ) + avg-pool-3x3( node-1 )
# node-3: skip-connect( node-0 ) + conv-3x3( node-1 ) + skip-connect( node-2 )

# Create the network from api:

In [23]:
config = api.get_net_config(arch, 'cifar10') # obtain the network configuration for the 123-th architecture on the CIFAR-10 dataset
print("config: ", config)
# from models import get_cell_based_tiny_net # this module is in AutoDL-Projects/lib/models
# network = get_cell_based_tiny_net(config) # create the network from configurration
# print(network) # show the structure of this architecture

Call the get_net_config function with index=15624, dataset=cifar10.
config:  {'name': 'infer.tiny', 'C': 16, 'N': 5, 'arch_str': '|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|', 'num_classes': 10}


# In nas_201_api, we define three classes: NASBench201API, ArchResults, ResultsCount.

### ResultsCount maintains all information of a specific trial. One can instantiate ResultsCount and get the info via the following codes (000157-FULL.pth saves all information of all trials of 157-th architecture):

In [30]:
xdata  = torch.load('/home/gean/datasets/NAS-Bench-201-v1_1-096897.pth')
odata  = xdata['full']['all_results'][('cifar100', 777)]
result = ResultsCount.create_from_state_dict( odata )
print(result) # print it
print(result.get_train())   # print the final training loss/accuracy/[optional:time-cost-of-a-training-epoch]
print(result.get_train(11)) # print the training info of the 11-th epoch
print(result.get_eval('x-valid'))     # print the final evaluation info on the validation set
print(result.get_eval('x-valid', 11)) # print the info on the validation set of the 11-th epoch
print(result.get_latency())           # print the evaluation latency [in batch]
result.get_net_param()                # the trained parameters of this trial
arch_config = result.get_config(CellStructure.str2structure) # create the network with params
net_config  = dict2config(arch_config, None)
network    = get_cell_based_tiny_net(net_config)
network.load_state_dict(result.get_net_param())

KeyError: 'all_results'

### ArchResults maintains all information of all trials of an architecture. Please see the following usages:

In [63]:
api.show(arch)

>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>> 012 epochs >>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>
|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|
datasets : ['cifar10-valid', 'cifar10', 'cifar100', 'ImageNet16-120'], extra-info : None
cifar10-valid  FLOP= 23.51 M, Params=0.185 MB, latency=19.55 ms.
cifar10-valid  train : [loss = 1.216, top1 = 56.05%], valid : [loss = 1.222, top1 = 55.76%]
cifar10        FLOP= 23.51 M, Params=0.185 MB, latency=19.55 ms.
cifar10        train : [loss = 0.965, top1 = 65.83%], test  : [loss = 0.944, top1 = 66.67%]
cifar100       FLOP= 23.52 M, Params=0.191 MB, latency=19.33 ms.
cifar100       train : [loss = 2.945, top1 = 25.85%], valid : [loss = 2.939, top1 = 25.28%], test : [loss = 2.947, top1 = 25.36%]
ImageNet16-120 FLOP=  5.89 M, Params=0.192 MB, latency=20.88 ms.
ImageNet16-120 train : [loss = 3.749, top1 = 12.89%], valid : [loss = 3.698, top1 = 13.43%], test : [loss = 3.716, top1 = 13.27%]
>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>

In [85]:
print("####### 12 epochs #######")
print("cifar10-valid:", api.statistics('cifar10-valid', 12))
print("cifar10:", api.statistics('cifar10', 12))
print("cifar100:", api.statistics('cifar100', 12))
print("ImageNet16-120:", api.statistics('ImageNet16-120', 12))

print("\n####### 200 epochs #######")
print("cifar10-valid:", api.statistics('cifar10-valid', 200))
print("cifar10:", api.statistics('cifar10', 200))
print("cifar100:", api.statistics('cifar100', 200))
print("ImageNet16-120:", api.statistics('ImageNet16-120', 200))


####### 12 epochs #######
Call the statistics function with dataset=cifar10-valid and hp=12.
cifar10-valid: {2: 15625}
Call the statistics function with dataset=cifar10 and hp=12.
cifar10: {1: 15625}
Call the statistics function with dataset=cifar100 and hp=12.
cifar100: {1: 15625}
Call the statistics function with dataset=ImageNet16-120 and hp=12.
ImageNet16-120: {1: 15625}

####### 200 epochs #######
Call the statistics function with dataset=cifar10-valid and hp=200.
cifar10-valid: {3: 7961, 2: 5439, 1: 2225}
Call the statistics function with dataset=cifar10 and hp=200.
cifar10: {3: 7961, 2: 5439, 1: 2225}
Call the statistics function with dataset=cifar100 and hp=200.
cifar100: {3: 7961, 2: 5439, 1: 2225}
Call the statistics function with dataset=ImageNet16-120 and hp=200.
ImageNet16-120: {3: 7961, 2: 5439, 1: 2225}


In [ ]:
num = len(api)

for i, arch_str in enumerate(api):
    print('{:5d}/{:5d} : {:}'.format(i, len(api), arch))

indexes = [1, 2, 11, 301]
for index in indexes:
    print('\n--- index={:} ---'.format(index))
    api.show(index)
    
    # show the mean loss and accuracy of an architecture
    info = api.query_meta_info_by_index(index)  # This is an instance of `ArchResults`
    res_metrics = info.get_metrics('cifar10', 'train') # This is a dict with metric names as keys
    cost_metrics = info.get_compute_costs('cifar100') # This is a dict with metric names as keys, e.g., flops, params, latency

    # get the detailed information
    results = api.query_by_index(index, 'cifar100') # a dict of all trials for 1st net on cifar100, where the key is the seed
    print('There are {:} trials for this architecture [{:}] on cifar100'.format(len(results), api[1]))
    
    for seed, result in results.items():
        print('Latency : {:}'.format(result.get_latency()))
        print('Train Info : {:}'.format(result.get_train()))
        print('Valid Info : {:}'.format(result.get_eval('x-valid')))
        print('Test  Info : {:}'.format(result.get_eval('x-test')))
          
        # for the metric after a specific epoch
        print ('Train Info [10-th epoch] : {:}'.format(result.get_train(10)))        
        config = api.get_net_config(index, 'cifar10')
        
        print ('config={:}'.format(config))

index = api.query_index_by_arch('|nor_conv_3x3~0|+|nor_conv_3x3~0|avg_pool_3x3~1|+|skip_connect~0|nor_conv_3x3~1|skip_connect~2|')
api.show(index)
print('TEST NAS-BENCH-201 DONE.')

In [88]:
info.get_compute_costs('cifar10')

{'flops': 23.51169,
 'params': 0.185306,
 'latency': 0.019546220177098325,
 'T-train@epoch': 20.89399222532908,
 'T-train@total': 250.72790670394895,
 'T-ori-test@epoch': 1.2722857111976258,
 'T-ori-test@total': 15.26742853437151}

### NASBench201API is the topest level api. Please see the following usages:

In [124]:
weights = api.get_net_param(arch, 'cifar100', None) # Obtaining the weights of all trials for the 3-th architecture on cifar10. It will returns a dict, where the key is the seed and the value is the trained weights.
weights

Call the get_net_param function with index=15624, dataset=cifar100, seed=None, hp=12
Call query_meta_info_by_index with arch_index=15624, hp=12


{111: None}

In [41]:
print("cifar10: ", api.get_more_info(112, 'cifar10', None, hp='200', is_random=True))
# Query info of last training epoch for 112-th architecture

# using 200-epoch-hyper-parameter and randomly select a trial.
print("\n\nImageNet16-120: ", api.get_more_info(112, 'ImageNet16-120', None, hp='200', is_random=True))

Call the get_more_info function with index=112, dataset=cifar10, iepoch=None, hp=200, and is_random=True.
Call query_index_by_arch with arch=112
cifar10:  {'train-loss': 0.011457711353600025, 'train-accuracy': 99.802, 'train-per-time': 15.465719938278198, 'train-all-time': 3093.1439876556396, 'test-loss': 0.3273583662033081, 'test-accuracy': 91.97, 'test-per-time': 1.1901337589536367, 'test-all-time': 238.02675179072736}
Call the get_more_info function with index=112, dataset=ImageNet16-120, iepoch=None, hp=200, and is_random=True.
Call query_index_by_arch with arch=112


ImageNet16-120:  {'train-loss': 2.1115262430375865, 'train-accuracy': 44.95583388226081, 'train-per-time': 46.922994292735936, 'train-all-time': 9384.598858547188, 'valid-loss': 2.408070919036865, 'valid-accuracy': 39.63333330281576, 'valid-per-time': 0.35704012768609095, 'valid-all-time': 71.4080255372182, 'test-loss': 2.3960227139790855, 'test-accuracy': 39.533333374023435, 'test-per-time': 0.35704012768609095, 'tes

# Genarate connection matrix/adjacency matrix from a string arch

In [42]:
api.str2matrix('|avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~1|+|nor_conv_1x1~0|skip_connect~1|skip_connect~2|')

array([[0., 0., 0., 0.],
       [4., 0., 0., 0.],
       [2., 1., 0., 0.],
       [2., 1., 1., 0.]])

In [141]:
nodes = api.str2lists('|avg_pool_3x3~0|+|nor_conv_1x1~0|none~1|+|nor_conv_3x3~0|skip_connect~1|skip_connect~2|')
print(len(nodes))
nodes

3


[(('avg_pool_3x3', 0),),
 (('nor_conv_1x1', 0), ('none', 1)),
 (('nor_conv_3x3', 0), ('skip_connect', 1), ('skip_connect', 2))]

In [153]:
#1-dim = node, 2-dim = edge, 3-dim = layer (0) or edge origin (1)
nodes[2][0:][0]

('nor_conv_3x3', 0)

In [44]:
arch = api.str2lists('|nor_conv_1x1~0|+|none~0|none~1|+|none~0|none~1|skip_connect~2|' )

print('there are {:} nodes in this arch'.format(len(arch)+1)) # arch is a list
for i, node in enumerate(arch):
    print('the {:}-th node is the sum of these {:} nodes with op: {:}'.format(i+1, len(node), node))

there are 4 nodes in this arch
the 1-th node is the sum of these 1 nodes with op: (('nor_conv_1x1', 0),)
the 2-th node is the sum of these 2 nodes with op: (('none', 0), ('none', 1))
the 3-th node is the sum of these 3 nodes with op: (('none', 0), ('none', 1), ('skip_connect', 2))


In [156]:
def extract_layers(api, arch_str) -> list:
    layers = []
    nodes = api.str2lists(arch_str)
    
    #there are always 3 nodes, besides node 0
    #1-dim = node, 2-dim = edge, 3-dim = layer (0) or edge origin (1)
    
    node_1 = nodes[0]
    layers.append(node_1[0][0])
    node_2 = nodes[1]
    layers.append(node_2[0][0])
    layers.append(node_2[1][0])
    node_3 = nodes[2]
    layers.append(node_3[0][0])
    layers.append(node_3[1][0])
    layers.append(node_3[2][0])
    
    return layers

In [157]:
print(extract_layers(api, '|avg_pool_3x3~0|+|nor_conv_1x1~0|none~1|+|nor_conv_3x3~0|skip_connect~1|skip_connect~2|'))

['avg_pool_3x3', 'nor_conv_1x1', 'none', 'nor_conv_3x3', 'skip_connect', 'skip_connect']


# Test

In [160]:
def extract_layers(api, arch_str) -> list:
    """
    there are always 3 nodes, besides node 0
    1-dim = node, 2-dim = edge, 3-dim = layer (0) or edge origin (1)
    i.e:
    input: |avg_pool_3x3~0|+|nor_conv_1x1~0|none~1|+|nor_conv_3x3~0|skip_connect~1|skip_connect~2|
    output: ['avg_pool_3x3', 'nor_conv_1x1', 'none', 'nor_conv_3x3', 'skip_connect', 'skip_connect']
    """
    
    layers = []
    nodes = api.str2lists(arch_str)
    
    node_1 = nodes[0]
    layers.append(node_1[0][0])
    node_2 = nodes[1]
    layers.append(node_2[0][0])
    layers.append(node_2[1][0])
    node_3 = nodes[2]
    layers.append(node_3[0][0])
    layers.append(node_3[1][0])
    layers.append(node_3[2][0])
    
    return layers

In [161]:
def get_arch_stats(layers : list) -> dict:
    remaining_arch_stats = {'avg_pool_num_layers': 0, 'skip_connection_num_layers': 0, 'zeroize_num_layers': 0}
    conv_layers = []
    
    for layer in layers:
        if layer == 'nor_conv_1x1': conv_layers.append(1)
        elif layer == 'nor_conv_3x3': conv_layers.append(3)
        elif layer == 'avg_pool_3x3': remaining_arch_stats['avg_pool_num_layers'] += 1
        elif layer == 'skip_connect': remaining_arch_stats['skip_connection_num_layers'] += 1
        elif layer == 'none': remaining_arch_stats['zeroize_num_layers'] += 1
        else: raise ValueError('Invalid layer type')
    
    conv_stats = extract_conv_stats(conv_layers) 
    
    return {**remaining_arch_stats, **conv_stats}

In [166]:
def extract_conv_stats(conv_layers : list) -> dict:
    conv_statistics = {'conv_num_layers': 0, 'conv_kernel_min': 0, 'conv_kernel_max': 0, 'conv_kernel_mode': 0}

    if len(conv_layers) > 0:
        conv_statistics['conv_num_layers'] = len(conv_layers)
        conv_statistics['conv_kernel_min'] = min(conv_layers) 
        conv_statistics['conv_kernel_max'] = max(conv_layers) 
        conv_statistics['conv_kernel_mode'] = stats.mode(conv_layers)[0][0]
  
    return conv_statistics

In [ ]:
for i, arch_str in enumerate(api):
    layers = extract_layers(api, arch_str)
    arch_stats = get_arch_stats(layers)
    print('{:} \n\n{:5d}/{:5d} : {:}\n\n'.format(str(arch_stats), i, len(api), arch_str))

# Extract all info available for an arch

In [177]:
arch_idx = 15624

>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>> 012 epochs >>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>
|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|
datasets : ['cifar10-valid', 'cifar10', 'cifar100', 'ImageNet16-120'], extra-info : None
cifar10-valid  FLOP= 23.51 M, Params=0.185 MB, latency=19.55 ms.
cifar10-valid  train : [loss = 1.216, top1 = 56.05%], valid : [loss = 1.222, top1 = 55.76%]
cifar10        FLOP= 23.51 M, Params=0.185 MB, latency=19.55 ms.
cifar10        train : [loss = 0.965, top1 = 65.83%], test  : [loss = 0.944, top1 = 66.67%]
cifar100       FLOP= 23.52 M, Params=0.191 MB, latency=19.33 ms.
cifar100       train : [loss = 2.945, top1 = 25.85%], valid : [loss = 2.939, top1 = 25.28%], test : [loss = 2.947, top1 = 25.36%]
ImageNet16-120 FLOP=  5.89 M, Params=0.192 MB, latency=20.88 ms.
ImageNet16-120 train : [loss = 3.749, top1 = 12.89%], valid : [loss = 3.698, top1 = 13.43%], test : [loss = 3.716, top1 = 13.27%]
>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>

In [207]:
# class:
# ArchResults
# methods: 
# get_compute_costs(self, dataset)
# get_metrics(self, dataset, setname, iepoch=None, is_random=False)

# legend: 
# datasets: cifar10-valid : training the model on the CIFAR-10 training set.
#           cifar10 : training the model on the CIFAR-10 training + validation set.
#           cifar100 : training the model on the CIFAR-100 training set.
#           ImageNet16-120 : training the model on the ImageNet16-120 training set.
            
# setname: for cifar10-valid -> 'train' (metric on train set), 'x-valid' (metric on validation set), 'ori-test' (metric on test set)
#          for cifar10 -> 'train' (metric on train + validation set), 'ori-test' (metric on test set)
#          for cifar100 and ImageNet16-120 -> 'train' (metric on train set), 'x-valid' (metric on validation set), 
#             'x-test' (metric on test set), 'ori-test' (metric on validation + test set)
            
# iepoch: None or an integer in [0, the-number-of-total-training-epochs)
#         None : return the metric after the last training epoch.
#         an integer i : return the metric after the i-th training epoch.            

# is_random: True : return the metric of a randomly selected trial.
#            False : return the averaged metric of all avaliable trials.
#            an integer indicating the 'seed' value : return the metric of a specific trial (whose random seed is 'is_random').


In [273]:
info = api.query_meta_info_by_index(arch_idx, hp='200')  # This is an instance of `ArchResults`
print("info: ", info)

model_metafeatures = {'id_arch': [], 'str_arch': [], 'layers_all': [], 'adjacency_matrix': [], 'dataset': [], 'setname': [], 'epoch': [], 
                      'flops': [], 'params': [], 'latency': [], 'time_train': [], 'time_val': [], 'time_test': [], 
                     'loss_train': [], 'loss_val': [], 'loss_test': [], 'acc_train': [], 'acc_val': [], 'acc_test': []}

datasets_setnames = {'cifar10-valid': ['train', 'x-valid', 'ori-test'], 
                     'cifar10': ['train', 'ori-test', ], 
                     'cifar100': ['train', 'x-valid', 'x-test', 'ori-test'], 
                     'ImageNet16-120': ['train', 'x-valid', 'x-test', 'ori-test']}

epochs = [0, 3, 11, 35, 107, 199]

for epoch in epochs:
    for dataset in datasets_setnames.keys():
        print("\n\n######## {} ########".format(dataset))
        
        cost_metrics = info.get_compute_costs(dataset)  
        print("\ncost_metrics: ", cost_metrics)
        
        for setname in datasets_setnames.get(dataset):
            try:
                res_metrics = info.get_metrics(dataset=dataset, setname=setname, iepoch=epoch, is_random=False) 
                print("{}: {}".format(setname, res_metrics))
                
            except KeyError as e:
                print("\ntype error: " + str(e), "\n")

Call query_meta_info_by_index with arch_index=15624, hp=200
info:  ArchResults(arch-index=15624, arch=|nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none~0|nor_conv_1x1~1|nor_conv_1x1~2|, 12 runs, clear=True)


######## cifar10-valid ########

cost_metrics:  {'flops': 23.51169, 'params': 0.185306, 'latency': 0.019546220177098325, 'T-train@epoch': 10.44699611266454, 'T-train@total': 2089.399222532908, 'T-x-valid@epoch': 3.1807142779940647, 'T-x-valid@total': 636.142855598813, 'T-ori-test@epoch': 1.272285711197626, 'T-ori-test@total': 254.45714223952518}
train: {'iepoch': 0.0, 'loss': 2.103105793088277, 'accuracy': 19.59466666320801, 'cur_time': 10.446996112664541, 'all_time': 10.446996112664541}
x-valid: {'iepoch': 0.0, 'loss': 2.047966608250936, 'accuracy': 22.168000002237957, 'cur_time': 3.180714277994065, 'all_time': 3.180714277994065}

type error: 'ori-test@0' 



######## cifar10 ########

cost_metrics:  {'flops': 23.51169, 'params': 0.185306, 'latency': 0.019546220177098325, 'T-train@e

In [276]:
'ori-test@0'[:-2]

'ori-test'

In [214]:
info.get_total_epoch('ImageNet16-120')

200